<a href="https://colab.research.google.com/github/aryan-bu/BA820/blob/main/Copy_of_BA820_Project.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import pandas as pd
data_test = '/content/drugsComTest_raw.tsv'
data_train = '/content/drugsComTrain_raw.tsv'

df_test = pd.read_csv(data_test, delimiter='\t')
df_train = pd.read_csv(data_train, delimiter='\t')

In [ ]:
df_test.head()

Unnamed: 0         drugName                     condition  \
0      163740      Mirtazapine                    Depression   
1      206473       Mesalamine  Crohn's Disease, Maintenance   
2      159672          Bactrim       Urinary Tract Infection   
3       39293         Contrave                   Weight Loss   
4       97768  Cyclafem 1 / 35                 Birth Control   

                                              review  rating  \
0  "I&#039;ve tried a few antidepressants over th...    10.0   
1  "My son has Crohn&#039;s disease and has done ...     8.0   
2                      "Quick reduction of symptoms"     9.0   
3  "Contrave combines drugs that were used for al...     9.0   
4  "I have been on this birth control for one cyc...     9.0   

                 date  usefulCount  
0   February 28, 2012           22  
1        May 17, 2009           17  
2  September 29, 2017            3  
3       March 5, 2017           35  
4    October 22, 2015            4

In [ ]:
df_train.head()

Unnamed: 0                  drugName                     condition  \
0      206461                 Valsartan  Left Ventricular Dysfunction   
1       95260                Guanfacine                          ADHD   
2       92703                    Lybrel                 Birth Control   
3      138000                Ortho Evra                 Birth Control   
4       35696  Buprenorphine / naloxone             Opiate Dependence   

                                              review  rating  \
0  "It has no side effect, I take it in combinati...     9.0   
1  "My son is halfway through his fourth week of ...     8.0   
2  "I used to take another oral contraceptive, wh...     5.0   
3  "This is my first time using any form of birth...     8.0   
4  "Suboxone has completely turned my life around...     9.0   

                date  usefulCount  
0       May 20, 2012           27  
1     April 27, 2010          192  
2  December 14, 2009           17  
3   November 3, 2015           10  
4  November 27, 2016           37

In [ ]:
df_test.shape

(53766, 7)

In [ ]:
df_train.shape

(161297, 7)

In [ ]:
df = pd.concat([df_test, df_train])
df.shape

(215063, 7)

In [ ]:
df = df.rename(columns={'Unnamed: 0': 'index'})
df = df.sort_values(by='index', ascending=True)
df.head()

index             drugName                  condition  \
47805       0  Medroxyprogesterone  Abnormal Uterine Bleeding   
93135       2  Medroxyprogesterone                 Amenorrhea   
143331      3  Medroxyprogesterone  Abnormal Uterine Bleeding   
57030       4  Medroxyprogesterone              Birth Control   
106347      5  Medroxyprogesterone  Abnormal Uterine Bleeding   

                                                   review  rating  \
47805   "Been on the depo injection since January 2015...     3.0   
93135   "I&#039;m 21 years old and recently found out ...    10.0   
143331  "I have been on the shot 11 years and until a ...     8.0   
57030   "Ive had four shots at this point. I was on bi...     9.0   
106347  "I had a total of 3 shots. I got my first one ...     1.0   

                    date  usefulCount  
47805   October 28, 2015            4  
93135   October 27, 2015           11  
143331  October 27, 2015            7  
57030   October 26, 2015           12  
106347  October 25, 2015            4

In [ ]:
df.isnull().sum()

index             0
drugName          0
condition      1194
review            0
rating            0
date              0
usefulCount       0
dtype: int64

In [ ]:
df = df.dropna()
df.isnull().sum()

index          0
drugName       0
condition      0
review         0
rating         0
date           0
usefulCount    0
dtype: int64

In [ ]:
duplicates = df[df.duplicated()]
duplicates

Empty DataFrame
Columns: [index, drugName, condition, review, rating, date, usefulCount]
Index: []

There are no duplicate values as well and we can move ahead with our analysis. Since the dataset is large, we can randomly select 20,000 rows for initial analysis.

In [ ]:
sample_df = df.sample(n=20000, random_state=42)
sample_df.shape

(20000, 7)

##Tokenization

In [ ]:
from nltk.tokenize import word_tokenize, wordpunct_tokenize, sent_tokenize, WhitespaceTokenizer
from nltk.tokenize.casual import TweetTokenizer
import nltk

In [ ]:
review_len = len(df['review'])
review_len

213869

###Sentence Tokenization

In [ ]:
tokenized = [[sent_tokenize(review)] for review in df['review']]
tokenized

[[['"Been on the depo injection since January 2015, had bleeding but it stopped after a while.',
   'When I had another injection in June, I didn&#039;t bleed for about a month.',
   'Started spotting mid-July and since approx.',
   'August 1st, I have been bleeding constantly, heavy enough to use pads and now it&#039;s almost November!',
   'I&#039;m sick of bleeding and forking out money for sanitary pads when I shouldn&#039;t be bleeding-well not as long as I have been now!',
   'Currently awaiting an ultrasound to see what is happening.',
   'I would like to change my contraceptive but my doctor won&#039;t let me :("']],
 [['"I&#039;m 21 years old and recently found out I might have PCOS.',
   'I haven&#039;t gotten my period since 2010.',
   'On October 13th 2015 I started taking medroxyprogesterone 10mg for 10 days.',
   'It actually worked.',
   'My period came on 4 days after finishing the pill.',
   'It started with very light cramping and very light bleeding.',
   'This is on

###Word Tokenization

In [ ]:
tokenized_word = [word_tokenize(review) for review in df['review']]
tokenized_word

[['``',
  'Been',
  'on',
  'the',
  'depo',
  'injection',
  'since',
  'January',
  '2015',
  ',',
  'had',
  'bleeding',
  'but',
  'it',
  'stopped',
  'after',
  'a',
  'while',
  '.',
  'When',
  'I',
  'had',
  'another',
  'injection',
  'in',
  'June',
  ',',
  'I',
  'didn',
  '&',
  '#',
  '039',
  ';',
  't',
  'bleed',
  'for',
  'about',
  'a',
  'month',
  '.',
  'Started',
  'spotting',
  'mid-July',
  'and',
  'since',
  'approx',
  '.',
  'August',
  '1st',
  ',',
  'I',
  'have',
  'been',
  'bleeding',
  'constantly',
  ',',
  'heavy',
  'enough',
  'to',
  'use',
  'pads',
  'and',
  'now',
  'it',
  '&',
  '#',
  '039',
  ';',
  's',
  'almost',
  'November',
  '!',
  'I',
  '&',
  '#',
  '039',
  ';',
  'm',
  'sick',
  'of',
  'bleeding',
  'and',
  'forking',
  'out',
  'money',
  'for',
  'sanitary',
  'pads',
  'when',
  'I',
  'shouldn',
  '&',
  '#',
  '039',
  ';',
  't',
  'be',
  'bleeding-well',
  'not',
  'as',
  'long',
  'as',
  'I',
  'have',
  'bee

###Punctuation Tokenization

In [ ]:
tokenized_punct = [WhitespaceTokenizer().tokenize(review) for review in df['review']]
tokenized_punct

[['"Been',
  'on',
  'the',
  'depo',
  'injection',
  'since',
  'January',
  '2015,',
  'had',
  'bleeding',
  'but',
  'it',
  'stopped',
  'after',
  'a',
  'while.',
  'When',
  'I',
  'had',
  'another',
  'injection',
  'in',
  'June,',
  'I',
  'didn&#039;t',
  'bleed',
  'for',
  'about',
  'a',
  'month.',
  'Started',
  'spotting',
  'mid-July',
  'and',
  'since',
  'approx.',
  'August',
  '1st,',
  'I',
  'have',
  'been',
  'bleeding',
  'constantly,',
  'heavy',
  'enough',
  'to',
  'use',
  'pads',
  'and',
  'now',
  'it&#039;s',
  'almost',
  'November!',
  'I&#039;m',
  'sick',
  'of',
  'bleeding',
  'and',
  'forking',
  'out',
  'money',
  'for',
  'sanitary',
  'pads',
  'when',
  'I',
  'shouldn&#039;t',
  'be',
  'bleeding-well',
  'not',
  'as',
  'long',
  'as',
  'I',
  'have',
  'been',
  'now!',
  'Currently',
  'awaiting',
  'an',
  'ultrasound',
  'to',
  'see',
  'what',
  'is',
  'happening.',
  'I',
  'would',
  'like',
  'to',
  'change',
  'my',
 

In [ ]:
nltk.download('vader_lexicon')

[nltk_data] Downloading package vader_lexicon to /root/nltk_data...


True

In [ ]:
from nltk.sentiment.vader import SentimentIntensityAnalyzer

In [ ]:
sentences = sent_tokenize(df['review'])

# Initialize the Sentiment Intensity Analyzer
sid = SentimentIntensityAnalyzer()

# Perform sentiment analysis on each sentence
segmented_text = []
for sentence in sentences:
    # Get the sentiment scores for the sentence
    sentiment_scores = sid.polarity_scores(sentence)
    # Determine the overall sentiment of the sentence
    if sentiment_scores['compound'] > 0.2:
        sentiment = 'positive'
    elif sentiment_scores['compound'] < -0.2:
        sentiment = 'negative'
    else:
        sentiment = 'neutral'
    # Append the segmented sentence along with its sentiment to the segmented text list
    segmented_text.append((sentence, sentiment))

# Print the segmented text with sentiment labels
for segment, sentiment in segmented_text:
    print(f"Segment: {segment} - Sentiment: {sentiment}")

TypeError: expected string or bytes-like object